In [1]:
import numpy as np
import csv
import os
import math

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [3]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [4]:
def CalculateMovements(AnnotData, Robustness):
  SumMovements = 0
  SumDistances = 0
  NumElements = 0
  CellMovements = []

  for cell_id in AnnotData.keys():
    prevx = AnnotData[cell_id][0].posx
    prevy = AnnotData[cell_id][0].posy
    MaxDist = 0
    CurrentMovement = 0
    for element in AnnotData[cell_id]:
      CurrentMovement += np.sqrt(np.power(element.posx-prevx,2)+np.power(element.posy-prevy,2))
      NumElements += 1
      prevx = element.posx
      prevy = element.posy
      DistFromZeroPos = np.sqrt(np.power(element.posx-AnnotData[cell_id][0].posx,2)+np.power(element.posy-AnnotData[cell_id][0].posy,2))
      if DistFromZeroPos>MaxDist:
        MaxDist = DistFromZeroPos
    SumDistances += MaxDist
    CellMovements.append(CurrentMovement)

  #Applying robust mean
  CellMovements.sort()
  if Robustness != 0:
    NumData = len(CellMovements)
    CellMovements = CellMovements[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumMovements = sum(CellMovements)

  SumMovements /= NumElements
  SumDistances /= NumElements
  return [SumMovements, SumDistances]

In [5]:
def UnitVector(vector):
    return vector / np.linalg.norm(vector)

def AngleBetween(v1, v2):
    v1_u = UnitVector(v1)
    v2_u = UnitVector(v2)
    return np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))

def CalculateAngles(AnnotData, Robustness):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if counter>2:
          Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])
          if not math.isnan(Angle):
            CurrentAngles += Angle
          pprevx = prevx
          pprevy = prevy
          prevx = element.posx
          prevy = element.posy
          NumElements += 1
        counter+=1
      CellAngles.append(CurrentAngles)

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumAngles = sum(CellAngles)/NumElements

  return [SumAngles]


In [6]:
def ReadData(CellType, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+"_shifted_trajectories.txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]
      

In [7]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/01 Videos')
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_10
BIBF_01_16
BIBF_01_7
BIBF_03_16
BIBF_03_6
aktivin01_2
aktivin01_3
hipox03_2
melanoma_GF01_11
zometa01_4
zometa01_6
zometa02_4
zometa03_3
zometa03_5
zometa06_3


In [8]:

#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/02 Human Annotations/"
ComputerDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Validisation data/03 Estimated Paths/"
OutCSVPath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation/Results/Calculations.csv"

with open(OutCSVPath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(['CellType','HumanAnnotatedMovements','HumanAnnotatedDistances','HumanAnnotatedAngles',
                      'ComputerAnnotatedMovements','ComputerAnnotatedDistances','ComputerAnnotatedAngles'])
  for CellType in CellTypes:
    #Reading both files
    [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,HumanDataFolder,ComputerDataFolder)

    #Calculating the movements for both data
    [HumanSumMovements, HumanSumDistances] = CalculateMovements(HumanAnnotData,0)
    [ComputerSumMovements, ComputerSumDistances] = CalculateMovements(ComputerAnnotData,0)
    [HumanSumAngles] = CalculateAngles(HumanAnnotData,0)
    [ComputerSumAngles] = CalculateAngles(ComputerAnnotData,0)

    print(CellType)
    print("  "+str(HumanSumMovements))
    print("  "+str(ComputerSumMovements))
    print()
    print("  "+str(HumanSumDistances))
    print("  "+str(ComputerSumDistances))
    print()
    print("  "+str(HumanSumAngles))
    print("  "+str(ComputerSumAngles))
    print()

    CSVwriter.writerow([CellType,HumanSumMovements,HumanSumDistances,HumanSumAngles,ComputerSumMovements,ComputerSumDistances,ComputerSumAngles])

    

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: RuntimeWarning: invalid value encountered in true_divide
  


BIBF06_10
  3.9152728053792503
  2.80167099755172

  1.1689887681539453
  1.3629682591945156

  0.14111276478341434
  1.2019232465156995

BIBF_01_16
  2.8323558215280102
  7.686547478151345

  0.6965926296495772
  2.417525625305755

  0.18597293050779215
  1.7210957611876698

BIBF_01_7
  11.190917235821448
  12.713607445469155

  2.637192990369355
  4.574329557087654

  0.54116667763346
  1.6802040054234382

BIBF_03_16
  11.202832773660766
  10.344798610987405

  3.24586400355857
  4.7386058784476495

  0.6705859326140493
  1.4032381104515026

BIBF_03_6
  0.36855862402277556
  3.883663843638115

  0.11870965893570966
  0.7556637513859101

  0.02290177290687767
  1.8161764300731147

aktivin01_2
  4.179893400994439
  3.9601755286971962

  1.2568579351829097
  1.4649747829066606

  0.3328246409002543
  1.4783951455402669

aktivin01_3
  4.107976087601958
  3.130395107482457

  1.2039024310452284
  1.2460201584872586

  0.2135675173800352
  1.3889113909988466

hipox03_2
  1.6815014039135308